In [ ]:
import cv2
import numpy as np
from matplotlib import pyplot as plt
from PIL import Image
from PIL.ExifTags import TAGS
from numpy import asarray
from numpy.fft import fft2, fftshift, fftfreq, ifft2 #Python DFT



In [ ]:
#imagename = "Data/crateres.jpg"
#imagename = "Data/Perseverance_ZR0_0074.png" -codigo adicional para recorte de bordes negros.
#imagename = "Data/mastcamz_2_prints.jpg"
imagename = "Data/Data_Mars_Mars8.png"
 
# read the image data using PIL
image = Image.open(imagename)

In [ ]:
display (image)

crateres.jpg : Image downloaded from : https://mars.nasa.gov/mars2020-raw-images/pub/ods/surface/sol/00000/ids/edr/browse/edl/ELM_0000_0666952859_600ECM_N0000030LVS_04000_0000LUJ00_800.jpg

Perseverance_ZR=_0074.png : Image downloaded from : 

In [ ]:
img = cv2.imread(imagename, 0) # load an image

#3 = np.asarray(imagename, dtype = np.float32)  # Image class instance, I1, to float32 Numpy array, a

img_float32 = np.float32(img)


Para procesar la imagen se lee como cv2.imread  y luego se le aplica la DFT 

DFT: Discrete Fourier Transform. 



In [ ]:
hist =cv2.calcHist([img],[0],None,[256],[0,256])
plt.plot(hist,color='blue')
plt.xlabel('Intensidad de Iluminacion')
plt.ylabel('Pixels Bins')
plt.show()

plt.hist(np.concatenate((img),axis=0),bins=250)
plt.xlabel('Intensidad de Iluminacion')
plt.ylabel('Pixels Bins')
plt.show()

In [ ]:
#transform,ar el array de la imagen en punto flotante para ser procesado. 
dft = cv2.dft(np.float32(img), flags=cv2.DFT_COMPLEX_OUTPUT)
dft_shift =np.fft.fftshift(dft)


In [ ]:
# convert image to numpy array 
data = asarray(image)
print(type(data))
# caracteristicas de la imagen
print(data.shape)


In [ ]:
#Muestra cada valor de cada pixel de la imagen como array en Numpy
#print(data)

In [ ]:
#imagen en el espacio de las frecuencias : 

f = np.fft.fft2(img) #fft2 para 2 dimensiones
fshift = np.fft.fftshift(f) # para centrar las frecuencias bajas.
#  fft2 tiene valors imaginarios por ello se saca el espectro real o de magnitud. 
magnitude_sprectrum = 20*np.log(np.abs(fshift)) 

In [ ]:
f.shape

In [ ]:
fft2(f)

In [ ]:
#Matplotlib para crear 2 subplots en la misma linea para comparar la imagen original y 
#la imagen transformada en el espectro de frecuencias. 
plt.subplot(121),plt.imshow(img , cmap = 'gray')
plt.title('Original Image'), plt.xticks([]),plt.yticks([])
plt.subplot(122),plt.imshow(magnitude_sprectrum , cmap = 'gray')
plt.title('Magnitude Spectrum'), plt.xticks([]),plt.yticks([])
plt.show


In [ ]:
#Filtro pasa alto HPF en el dominio de las frencuencias para demarcar contornos: 


rows, cols = img.shape
crow, ccol = int(rows/2), int(cols/2)

#remover las frecuencias bajas usando una plantilla circular 

mask=np.ones((rows,cols,2),np.uint8)
r = 40
center = [crow, ccol]
x, y = np.ogrid[:rows, :cols]
mask_area = (x - center[0]) ** 2 + (y - center[1]) ** 2 <= r*r
mask[mask_area] = 1

fshift=dft_shift*mask

fshift_mask_mag=2000*np.log(cv2.magnitude(fshift[:,:,0],fshift[:,:,1]))

f_ishift =np.fft.ifftshift(fshift)
img_back =cv2.idft(f_ishift)
img_back =cv2.magnitude(img_back[:,:,0],img_back[:,:,1])

#fshift[crow-30:crow+30,ccol-30:ccol+30]=0


f_ishift = np.fft.ifftshift(fshift)

img_back = np.fft.ifft2(f_ishift)

img_back = np.abs(img_back)



In [ ]:
#Filtro pasa Banda BPF  aplicando dos circulos concentricos

rows, cols = img.shape
crow, ccol = int(rows/2), int(cols/2)  # circulo centro


#remover las frecuencias bajas usando una plantilla circular 

rows, cols = img.shape
crow, ccol = int(rows/2), int(cols/2)

mask=np.zeros((rows,cols,2),np.uint8)
r_out = 40
r_in = 4
center = [crow, ccol]
x, y = np.ogrid[:rows, :cols]

mask_area = np.logical_and(((x-center[0])**2 +(y-center[1])**2>= r_in**2),
                          ((x-center[0])**2 +(y-center[1])**2<= r_out**2))
                            
   
mask[mask_area] = 1

fshift=dft_shift*mask

fshift_mask_mag= 2000 * np.log(cv2.magnitude(fshift[:, :, 0], fshift[:, :, 1]))

f_ishift =np.fft.ifftshift(fshift)
img_back =cv2.idft(f_ishift)
img_back =cv2.magnitude(img_back[:,:,0],img_back[:,:,1])

#fshift[crow-30:crow+30,ccol-30:ccol+30]=0

fig = plt.figure(figsize=(20,20))

fig.add_subplot(2, 2, 1), plt.imshow(img, cmap='gray')
plt.title('Input Image'), plt.xticks([]), plt.yticks([])
fig.add_subplot(2, 2, 2), plt.imshow(magnitude_sprectrum,cmap='gray')
plt.title('After FFT'), plt.xticks([]), plt.yticks([])
fig.add_subplot(2, 2, 3), plt.imshow(fshift_mask_mag, cmap='gray')
plt.title('FFT + Mask'), plt.xticks([]), plt.yticks([])
fig.add_subplot(2, 2, 4), plt.imshow(img_back, cmap='gray')
plt.title('After FFT Inverse'), plt.xticks([]), plt.yticks([])
plt.show()

In [ ]:
#Filtro pasa Banda BPF  aplicando dos circulos concentricos

rows, cols = img.shape
crow, ccol = int(rows/2), int(cols/2)  # circulo centro


#remover las frecuencias bajas usando una plantilla circular 

rows, cols = img.shape
crow, ccol = int(rows/2), int(cols/2)

mask=np.zeros((rows,cols,2),np.uint8)

#con diferentes radios tal que sean mayor que la zona central, tapando la mayor cantidad de bajas frencuencias. 
r_out = 80
r_in = 4
center = [crow, ccol]
x, y = np.ogrid[:rows, :cols]

mask_area = np.logical_and(((x-center[0])**2 +(y-center[1])**2>= r_in**2),
                          ((x-center[0])**2 +(y-center[1])**2<= r_out**2))
                            
   
mask[mask_area] = 1

fshift=dft_shift*mask

fshift_mask_mag= 2000 * np.log(cv2.magnitude(fshift[:, :, 0], fshift[:, :, 1]))

f_ishift =np.fft.ifftshift(fshift)
img_back =cv2.idft(f_ishift)
img_back =cv2.magnitude(img_back[:,:,0],img_back[:,:,1])




fig = plt.figure(figsize=(20,20))

fig.add_subplot(121),plt.imshow(img , cmap = 'gray')
plt.title('Original Image'), plt.xticks([]),plt.yticks([])
fig.add_subplot(122),plt.imshow(img_back , cmap = 'gray')
plt.title('AFTER FFT Inverse image'), plt.xticks([]),plt.yticks([])
plt.show()

In [ ]:
plt.subplot(131),plt.imshow(img, cmap='gray')
plt.title('Input Image'), plt.xticks([]), plt.yticks([])
plt.subplot(132),plt.imshow(img_back , cmap = 'gray')
plt.title('Imagen con HPF'), plt.xticks([]),plt.yticks([])
plt.subplot(133),plt.imshow(img_back)
plt.title('Imagen Final'), plt.xticks([]),plt.yticks([])
plt.show

In [ ]:
fig = plt.figure(figsize=(20,20))

fig.add_subplot(121),plt.imshow(img , cmap = 'gray')
plt.title('Original Image'), plt.xticks([]),plt.yticks([])
fig.add_subplot(122),plt.imshow(img_back , cmap = 'gray')
plt.title('HPF image'), plt.xticks([]),plt.yticks([])
plt.show


In [ ]:
#Comparativa para la foto de las rocas 
#recortado de foto 
#Recortar una imagen
crop= img[200:400,200:500]


cv2.imshow('Seccion Imagen',crop)

In [ ]:
#filtro Pasa bajos: LPF

dft_shift= np.fft.fftshift(dft)

rows, cols = img.shape

crow , ccol = int(rows/2), int(cols/2)  

mask= np.zeros((rows,cols,2),np.uint8)
mask[crow-30:crow+30,ccol-30:ccol+30]=1


fshift = dft_shift*mask
f_ishift=np.fft.ifftshift(fshift)
img_back=cv2.idft(f_ishift)
img_back=cv2.magnitude(img_back[:,:,0],img_back[:,:,1])

In [ ]:
fig = plt.figure(figsize=(20,20))

fig.add_subplot(121),plt.imshow(img , cmap = 'gray')
plt.title('Original Image'), plt.xticks([]),plt.yticks([])
fig.add_subplot(122),plt.imshow(img_back , cmap = 'gray')
plt.title('LPF image'), plt.xticks([]),plt.yticks([])
plt.show
